In [1]:
import weaviate

client = weaviate.connect_to_local()


In [2]:
COLBERT_CLASS_NAME="jqara_colbert"
MUVERA_CLASS_NAME = "jqara_muvera"

In [3]:
from weaviate.classes.config import Configure, Property, DataType

if client.collections.exists(COLBERT_CLASS_NAME):
    client.collections.delete(COLBERT_CLASS_NAME)

client.collections.create(
    name=COLBERT_CLASS_NAME,
    vector_config=[
        # User-provided embeddings
        Configure.MultiVectors.self_provided(
            name="multi_vector",
        ),
    ],
    properties=[
        Property(name="d_id", data_type=DataType.TEXT),
        Property(name="title", data_type=DataType.TEXT),
        Property(name="text", data_type=DataType.TEXT),
    ],
)

In [36]:
from weaviate.classes.config import Configure, Property, DataType

if client.collections.exists(MUVERA_CLASS_NAME):
    client.collections.delete(MUVERA_CLASS_NAME)

client.collections.create(
    name=MUVERA_CLASS_NAME,
    vector_config=[
        # User-provided embeddings
        Configure.MultiVectors.self_provided(
            name="multi_vector",
            encoding=Configure.VectorIndex.MultiVector.Encoding.muvera(),
        ),
    ],
    properties=[
        Property(name="d_id", data_type=DataType.TEXT),
        Property(name="q_id", data_type=DataType.TEXT, index_filterable=True),  # フィルタ用にインデックス
        Property(name="title", data_type=DataType.TEXT),
        Property(name="text", data_type=DataType.TEXT),
    ],
)

In [37]:
colbert_col = client.collections.get(COLBERT_CLASS_NAME)
muvera_col = client.collections.get(MUVERA_CLASS_NAME)

col = muvera_col

In [38]:
import json
import os

dataset = []
current_dir = os.getcwd()
file_path = os.path.join(current_dir, "data", "jqara_test.jsonl")
with open(file_path, "r", encoding="utf-8") as f:
    for line in f:
        if not line.strip():
            continue
        obj = json.loads(line)        
        dataset.append(obj)

print(dataset[0])        

{'id': 'QA20CAPR-1004#5191928', 'q_id': 'QA20CAPR-1004', 'passage_row_id': '5191928', 'label': 1, 'text': '絶対零度(ぜったいれいど、アブソリュートゼロ、英: Absolute zero)は、熱力学上の最低温度である摂氏−273.15度。', 'title': '絶対零度 (曖昧さ回避)', 'question': '摂氏ではマイナス273.15度にあたる、全ての原子の振動が停止する最も低い温度を何というでしょう?', 'answers': ['絶対零度']}


In [7]:
import glob
import torch

current_dir = os.getcwd()
batch_paths = sorted(glob.glob(os.path.join(current_dir, "outputs/jacolbert", "batch_*.pt")))

ids = []
embeddings = []  # List[Tensor[n_tokens, dim]]

for p in batch_paths:
    payload = torch.load(p, map_location="cpu")
    ids.extend([str(x) for x in payload.get("ids", [])])
    for e in payload.get("embeddings", []):
        if isinstance(e, torch.Tensor):
            embeddings.append(e.detach().to("cpu").contiguous())
        else:
            embeddings.append(torch.as_tensor(e, dtype=torch.float32))

assert len(ids) == len(embeddings)

print("batches:", len(batch_paths), "docs:", len(embeddings))

batches: 326 docs: 166700


In [39]:
print(dataset[166699])
print(ids[166699])
print(embeddings[166699])

{'id': 'QA20QBIK-2000#4794232', 'q_id': 'QA20QBIK-2000', 'passage_row_id': '4794232', 'label': 0, 'text': 'これは、1973年のビルボード・ホット100による1位のシングル一覧である。背景色を黄色にしているものは、1973年の年間チャートで1位になった楽曲である。', 'title': '1973年のビルボード・ホット100による1位のシングル一覧', 'question': '1977年、アメリカのバンド・イーグルスが放った、砂漠に建つ架空のホテルを舞台にした全米ナンバー1ソングは何?', 'answers': ['ホテル・カリフォルニア']}
QA20QBIK-2000#4794232
tensor([[ 0.1615,  0.1130, -0.1672,  ...,  0.0103, -0.0216, -0.0463],
        [ 0.1477,  0.0896, -0.0544,  ..., -0.0267,  0.1017, -0.0957],
        [ 0.0771,  0.0824, -0.0220,  ..., -0.0178,  0.0833, -0.1333],
        ...,
        [ 0.0711,  0.0994, -0.0850,  ..., -0.0547,  0.0049, -0.0147],
        [ 0.1274,  0.0717, -0.1174,  ..., -0.0082,  0.0231,  0.0080],
        [ 0.0973,  0.0362, -0.0545,  ..., -0.0215,  0.0103,  0.0524]])


In [40]:
from tqdm import tqdm

N = 166700
# N = 66700
subset = dataset[:N]
emb_subset = embeddings[:N]

total = len(subset)

# tqdmで進捗バーを表示
with col.batch.fixed_size(batch_size=16) as batch, tqdm(total=total, desc="📤 Uploading to Weaviate") as pbar:
    for obj, emb in zip(subset, emb_subset):
        # オブジェクトを追加
        batch.add_object(
            properties={
                "d_id": obj["id"],
                "q_id": obj["q_id"],  # q_idを追加
                "text": obj["text"],
                "title": obj["title"],
            },
            vector={"multi_vector": emb.tolist()},
        )

        # 進捗更新
        pbar.update(1)

# 全体完了後のチェック
if col.batch.failed_objects:
    print(f"\n❌ Number of failed imports: {len(col.batch.failed_objects)}")
    print(f"First failed object: {col.batch.failed_objects[0]}")
else:
    print("\n✅ All objects uploaded successfully!")

# コレクション内の件数を確認
count = col.aggregate.over_all(total_count=True).total_count
print(f"🧮 現在の登録件数: {count}")

📤 Uploading to Weaviate: 100%|██████████| 166700/166700 [06:19<00:00, 439.62it/s]



✅ All objects uploaded successfully!
🧮 現在の登録件数: 166700


In [ ]:
from colbert.infra import ColBERTConfig
from colbert.modeling.checkpoint import Checkpoint

ckpt = Checkpoint("jinaai/jina-colbert-v2", colbert_config=ColBERTConfig())

In [41]:

ckpt = Checkpoint("bclavie/JaColBERT", colbert_config=ColBERTConfig())

/Users/satoshi.takatori.001/Desktop/playground/weaviate-sample/.venv/lib/python3.12/site-packages/colbert/utils/amp.py:12: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  self.scaler = torch.cuda.amp.GradScaler()
/Users/satoshi.takatori.001/Desktop/playground/weaviate-sample/.venv/lib/python3.12/site-packages/torch/cuda/amp/grad_scaler.py:31: UserWarning: torch.cuda.amp.GradScaler is enabled, but CUDA is not available.  Disabling.
  super().__init__(


In [42]:
q = subset[600]["question"]

q_vecs = ckpt.queryFromText([q], bsize=1)[0]
print(q_vecs)
print(len(q_vecs))


tensor([[-0.0795,  0.0506, -0.0372,  ...,  0.0853, -0.1266, -0.0209],
        [-0.0320, -0.0024,  0.0659,  ...,  0.0349,  0.0084,  0.0452],
        [ 0.0259, -0.0022,  0.0240,  ...,  0.0968,  0.0656,  0.0342],
        ...,
        [-0.0195, -0.0201,  0.0244,  ..., -0.0054, -0.0255,  0.0256],
        [ 0.0374, -0.0081,  0.0484,  ...,  0.0998, -0.0032,  0.0949],
        [-0.0227,  0.0643,  0.0146,  ...,  0.1327, -0.1094,  0.1478]])
32


/Users/satoshi.takatori.001/Desktop/playground/weaviate-sample/.venv/lib/python3.12/site-packages/colbert/utils/amp.py:15: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  return torch.cuda.amp.autocast() if self.activated else NullContextManager()
/Users/satoshi.takatori.001/Desktop/playground/weaviate-sample/.venv/lib/python3.12/site-packages/torch/amp/autocast_mode.py:270: UserWarning: User provided device_type of 'cuda', but CUDA is not available. Disabling
  warnings.warn(


In [43]:
from weaviate.classes.query import MetadataQuery


q = subset[0]["question"]
print(q)
q_vecs = ckpt.queryFromText([q], bsize=1)[0]  # [Lq, dim]

response = col.query.near_vector(
    near_vector=q_vecs.tolist(),
    target_vector="multi_vector",
    return_metadata=MetadataQuery(distance=True, certainty=True, score=True),
    limit=1000
)

for o in response.objects:
    title = (o.properties or {}).get("title")
    text = (o.properties or {}).get("text") or ""
    # near_text なら通常 distance / certainty が入る（要求した場合）
    dist = getattr(o.metadata, "distance", None)
    cert = getattr(o.metadata, "certainty", None)
    score = getattr(o.metadata, "score", None)  # ハイブリッド/BM25で付くことがある
    # どれが取得できたかで柔軟に表示
    if dist is not None:
        metric = f"distance={dist:.4f}"
    elif score is not None:
        metric = f"score={score:.4f}"
    elif cert is not None:
        metric = f"certainty={cert:.4f}"
    else:
        metric = "(no metric)"

    print(f"- {metric}  title: {title}")
    print(f"  text: {text[:120]}...")
    print(f"  q_id: {(o.properties or {}).get('q_id')}, answers: {(o.properties or {}).get('answers')}\n")


摂氏ではマイナス273.15度にあたる、全ての原子の振動が停止する最も低い温度を何というでしょう?
- distance=-24.3859  title: 絶対零度
  text: 温度は、物質の熱振動をもとにして規定されているので、下限が存在する。それは、熱振動(原子の振動)が小さくなり、エネルギーが最低になった状態である。この時に決まる下限温度が絶対零度である。古典力学では、エネルギーが最低の状態とは、原子の振動が...
  q_id: QA20QBIK-1097, answers: None

- distance=-24.3859  title: 絶対零度
  text: 温度は、物質の熱振動をもとにして規定されているので、下限が存在する。それは、熱振動(原子の振動)が小さくなり、エネルギーが最低になった状態である。この時に決まる下限温度が絶対零度である。古典力学では、エネルギーが最低の状態とは、原子の振動が...
  q_id: QA20CAPR-1004, answers: None

- distance=-24.3859  title: 絶対零度
  text: 温度は、物質の熱振動をもとにして規定されているので、下限が存在する。それは、熱振動(原子の振動)が小さくなり、エネルギーが最低になった状態である。この時に決まる下限温度が絶対零度である。古典力学では、エネルギーが最低の状態とは、原子の振動が...
  q_id: QA20QBIK-1214, answers: None

- distance=-24.1298  title: 絶対零度 (曖昧さ回避)
  text: 絶対零度(ぜったいれいど、アブソリュートゼロ、英: Absolute zero)は、熱力学上の最低温度である摂氏−273.15度。...
  q_id: QA20QBIK-1214, answers: None

- distance=-24.1298  title: 絶対零度 (曖昧さ回避)
  text: 絶対零度(ぜったいれいど、アブソリュートゼロ、英: Absolute zero)は、熱力学上の最低温度である摂氏−273.15度。...
  q_id: QA20CAPR-1004, answers: None

- distance=-24.1298  title: 絶

In [44]:
result = col.aggregate.over_all(total_count=True)

print("📊 登録ドキュメント数:", result.total_count)

📊 登録ドキュメント数: 166700


In [45]:
nodes = client.cluster.nodes(output="verbose") # verboseで詳細情報を取得

for node in nodes:
    print(f"Node Name: {node.name}")
    print(f"Status: {node.status}")
    
    # シャードごとの統計情報
    if node.shards:
        for shard in node.shards:
            print(f"  - Class: {shard}")
            print(f"    Object Count: {shard.object_count}")
            # ベクトルインデックスやストレージの情報などを含んでいる場合があります
            # バージョンや設定により取得できるフィールドが異なる可能性があります
    print("-" * 20)



Node Name: node1
Status: HEALTHY
  - Class: Shard(collection='Jqara', name='hvbyMVyy0J5r', node='node1', object_count=5000, vector_indexing_status='READY', vector_queue_length=0, compressed=False, loaded=True)
    Object Count: 5000
  - Class: Shard(collection='Jqara_bm25', name='HJFZSJtNfOGr', node='node1', object_count=66700, vector_indexing_status='READY', vector_queue_length=0, compressed=False, loaded=True)
    Object Count: 66700
  - Class: Shard(collection='Jqara_muvera', name='MVcPSfmCTwBo', node='node1', object_count=166700, vector_indexing_status='READY', vector_queue_length=0, compressed=False, loaded=True)
    Object Count: 166700
  - Class: Shard(collection='Question', name='C4gDZIHzIBb3', node='node1', object_count=10, vector_indexing_status='READY', vector_queue_length=0, compressed=False, loaded=True)
    Object Count: 10
  - Class: Shard(collection='Jqara_colbert', name='9ZBYsRXm7naO', node='node1', object_count=0, vector_indexing_status='READY', vector_queue_length=0,

In [46]:
from typing import Dict, List, Tuple, Iterable


qid_to_query: Dict[str, str] = {}
qrels: Dict[str, Dict[str, int]] = {}

cnt = 0
for rec in subset:
    cnt += 1
    qid   = rec["q_id"]
    q = rec.get("question")
    docid = rec.get("id")
    rel   = int(rec.get("label", 0))

    if qid not in qid_to_query:
        qid_to_query[qid] = q
    qrels.setdefault(qid, {})[docid] = rel

print(f"Loaded {cnt} records")
print(f"Unique queries: {len(qid_to_query)}")

Loaded 166700 records
Unique queries: 1667


In [55]:
from typing import Callable, Awaitable, List, Tuple, Dict
import asyncio

async def build_run_dict_async(
        search_fn: Callable[[str, int], Awaitable[Tuple[List[Tuple[str, float]], float]]],
        qid_to_query: Dict[str, str],
        topk: int = 100
    ) -> Tuple[Dict[str, Dict[str, float]], List[float]]:
    """
    非同期検索関数を使って全クエリを実行し、run_dictとlatenciesを返す。
    
    Args:
        search_fn: (q, topk) -> ([(doc_id, score), ...], elapsed)
        qid_to_query: {qid: query_text} の辞書
        topk: 各クエリで取得する件数
        
    Returns:
        run_dict: {qid: {doc_id: score, ...}, ...}
        latencies: 各クエリのレイテンシリスト
    """
    CONCURRENCY = 10
    sem = asyncio.Semaphore(CONCURRENCY)    
    run_dict: Dict[str, Dict[str, float]] = {}
    latencies: List[float] = []

    async def _one(qid: str, q: str):
        async with sem:
            ranked, elapsed = await search_fn(q, topk)
            return qid, ranked, elapsed

    tasks = [_one(qid, q) for qid, q in qid_to_query.items()]
    
    for coro in tqdm(asyncio.as_completed(tasks), total=len(tasks), desc="Searching"):
        qid, ranked, elapsed = await coro
        run_dict[qid] = {doc_id: score for doc_id, score in ranked}
        latencies.append(elapsed)
    
    return run_dict, latencies


async def build_run_dict_async_with_qid(
        search_fn: Callable[[str, str, int], Awaitable[Tuple[List[Tuple[str, float]], float]]],
        qid_to_query: Dict[str, str],
        topk: int = 100
    ) -> Tuple[Dict[str, Dict[str, float]], List[float]]:
    """
    非同期検索関数を使って全クエリを実行し、run_dictとlatenciesを返す。
    q_idでフィルタリングするバージョン。
    
    Args:
        search_fn: (q, q_id, topk) -> ([(doc_id, score), ...], elapsed)
        qid_to_query: {qid: query_text} の辞書
        topk: 各クエリで取得する件数
        
    Returns:
        run_dict: {qid: {doc_id: score, ...}, ...}
        latencies: 各クエリのレイテンシリスト
    """
    CONCURRENCY = 10
    sem = asyncio.Semaphore(CONCURRENCY)    
    run_dict: Dict[str, Dict[str, float]] = {}
    latencies: List[float] = []

    async def _one(qid: str, q: str):
        async with sem:
            ranked, elapsed = await search_fn(q, qid, topk)  # q_idを渡す
            return qid, ranked, elapsed

    tasks = [_one(qid, q) for qid, q in qid_to_query.items()]
    
    for coro in tqdm(asyncio.as_completed(tasks), total=len(tasks), desc="Searching"):
        qid, ranked, elapsed = await coro
        run_dict[qid] = {doc_id: score for doc_id, score in ranked}
        latencies.append(elapsed)
    
    return run_dict, latencies

In [56]:

async_client = weaviate.use_async_with_local()
await async_client.connect()

async_col = async_client.collections.get(MUVERA_CLASS_NAME)
q = subset[600]["question"]

q_vecs = ckpt.queryFromText([q], bsize=1)[0]  # [Lq, dim]
print(q)
print(q_vecs)
print(len(q_vecs))

response = async_col.query.near_vector(
    near_vector=q_vecs.tolist(),
    target_vector="multi_vector",
    return_metadata=MetadataQuery(distance=True, certainty=True, score=True)
)

res = await response

print(res)



星条旗といえばアメリカの国旗ですが、太極旗といえばどこの国旗でしょう?
tensor([[-0.0795,  0.0506, -0.0372,  ...,  0.0853, -0.1266, -0.0209],
        [-0.0320, -0.0024,  0.0659,  ...,  0.0349,  0.0084,  0.0452],
        [ 0.0259, -0.0022,  0.0240,  ...,  0.0968,  0.0656,  0.0342],
        ...,
        [-0.0195, -0.0201,  0.0244,  ..., -0.0054, -0.0255,  0.0256],
        [ 0.0374, -0.0081,  0.0484,  ...,  0.0998, -0.0032,  0.0949],
        [-0.0227,  0.0643,  0.0146,  ...,  0.1327, -0.1094,  0.1478]])
32


In [57]:
from typing import List, Tuple
from weaviate.classes.query import MetadataQuery, Filter
import time

async def async_muvera_search(async_col, q: str, q_id: str, topk: int = 100) -> Tuple[List[Tuple[str, float]], float]:
    """
    ColBERT (Multi-vector) を用いた非同期検索関数
    q_idでフィルタリングして、該当クエリの候補文書群の中からランキング
    
    Args:
        async_col: 非同期Weaviateコレクション
        q: 検索クエリ文字列
        q_id: フィルタ用のクエリID
        topk: 取得する件数
        
    Returns:
        ([(doc_id, score), ...], elapsed) のタプル
        scoreは大きいほど良い（distanceを反転）
    """
    # クエリのベクトル化 (ColBERT)
    q_vecs_tensor = ckpt.queryFromText([q], bsize=1)[0]
    q_vecs = q_vecs_tensor.tolist()

    # 非同期クエリの実行（q_idでフィルタリング）
    start = time.perf_counter()

    response = await async_col.query.near_vector(
        near_vector=q_vecs,
        target_vector="multi_vector",
        limit=topk,
        filters=Filter.by_property("q_id").equal(q_id),
        return_metadata=MetadataQuery(distance=True)
    )

    elapsed = time.perf_counter() - start

    # 結果の整形: (doc_id, score) のリスト
    # ranxは大きいスコアを上位とするため、distanceを反転（負にする）
    results: List[Tuple[str, float]] = []
    for obj in response.objects:
        doc_id = obj.properties.get("d_id", "")
        score = -obj.metadata.distance  # 距離を反転！
        results.append((doc_id, score))

    return results, elapsed


def create_muvera_search_fn(async_col):
    """async_colをバインドした検索関数を返すファクトリ（q_id対応版）"""
    async def search_fn(q: str, q_id: str, topk: int = 100) -> Tuple[List[Tuple[str, float]], float]:
        return await async_muvera_search(async_col, q, q_id, topk)
    return search_fn

In [58]:
# async with で接続ライフサイクルを管理（q_idフィルタリング版の動作確認）
async with weaviate.use_async_with_local() as async_client:
    
    # 最初のクエリで動作確認
    first_qid = next(iter(qid_to_query.keys()))
    query_text = qid_to_query[first_qid]
    print(f"Query: {query_text}")
    print(f"q_id: {first_qid}")
    
    async_col = async_client.collections.get(MUVERA_CLASS_NAME)
    # 関数呼び出し（q_idでフィルタリング）
    hits, elapsed = await async_muvera_search(async_col, query_text, first_qid, topk=10)
    
    # 結果表示 (hitsは [(doc_id, score), ...] の形式)
    print(f"\n検索結果（q_id={first_qid}の候補文書内でランキング）:")
    for doc_id, score in hits:
        print(f"Score: {score:.4f} | doc_id: {doc_id}")

    print(f"\nElapsed: {elapsed:.4f} seconds")

Query: 摂氏ではマイナス273.15度にあたる、全ての原子の振動が停止する最も低い温度を何というでしょう?
q_id: QA20CAPR-1004

検索結果（q_id=QA20CAPR-1004の候補文書内でランキング）:
Score: 24.3859 | doc_id: QA20CAPR-1004#60221
Score: 24.1298 | doc_id: QA20CAPR-1004#5191928
Score: 24.0660 | doc_id: QA20CAPR-1004#60220
Score: 23.8120 | doc_id: QA20CAPR-1004#49522
Score: 22.4734 | doc_id: QA20CAPR-1004#2503329
Score: 22.0413 | doc_id: QA20CAPR-1004#220130
Score: 22.0214 | doc_id: QA20CAPR-1004#2457942
Score: 21.6903 | doc_id: QA20CAPR-1004#2665789
Score: 21.4613 | doc_id: QA20CAPR-1004#3058892
Score: 21.3546 | doc_id: QA20CAPR-1004#192230

Elapsed: 0.0264 seconds


In [59]:
from tqdm import tqdm

# build_run_dict_async_with_qid を使って全クエリを検索（q_idフィルタリング版）

muvera_search_run_dict = {}
muvera_search_latencies = []

async with weaviate.use_async_with_local() as async_client:
    async_col = async_client.collections.get(MUVERA_CLASS_NAME)
    
    # async_col をバインドした検索関数を作成
    search_fn = create_muvera_search_fn(async_col)
    
    # 全クエリを実行（q_idでフィルタリング）
    muvera_search_run_dict, muvera_search_latencies = await build_run_dict_async_with_qid(
        search_fn, 
        qid_to_query,
        topk=100  # 各q_idに対応する全ドキュメントを取得
    )

print(f"検索完了: {len(muvera_search_run_dict)} クエリ")
print(f"平均レイテンシ: {sum(muvera_search_latencies) / len(muvera_search_latencies):.4f} 秒")

Searching: 100%|██████████| 1667/1667 [00:42<00:00, 39.16it/s]

検索完了: 1667 クエリ
平均レイテンシ: 0.1789 秒


In [60]:
muvera_search_run_dict

{'QA20QBIK-1532': {'QA20QBIK-1532#960671': 26.813817977905273,
  'QA20QBIK-1532#522297': 26.519853591918945,
  'QA20QBIK-1532#2081072': 26.484445571899414,
  'QA20QBIK-1532#394913': 25.840396881103516,
  'QA20QBIK-1532#2519252': 25.81182098388672,
  'QA20QBIK-1532#938632': 25.72501564025879,
  'QA20QBIK-1532#1533336': 25.717191696166992,
  'QA20QBIK-1532#2290695': 25.499731063842773,
  'QA20QBIK-1532#390225': 25.494291305541992,
  'QA20QBIK-1532#1069574': 25.440649032592773,
  'QA20QBIK-1532#2978874': 25.406719207763672,
  'QA20QBIK-1532#1544925': 25.38970184326172,
  'QA20QBIK-1532#3132773': 25.365388870239258,
  'QA20QBIK-1532#990615': 25.265850067138672,
  'QA20QBIK-1532#377696': 25.147855758666992,
  'QA20QBIK-1532#2117102': 25.11495590209961,
  'QA20QBIK-1532#3991896': 25.007123947143555,
  'QA20QBIK-1532#377697': 25.00018310546875,
  'QA20QBIK-1532#274430': 24.990978240966797,
  'QA20QBIK-1532#858435': 24.974092483520508,
  'QA20QBIK-1532#10029': 24.920698165893555,
  'QA20QBIK-1

In [63]:
from ranx import Qrels, Run, evaluate

def evaluate_run_dict(run_dict: Dict[str, Dict[str, float]], qrels: Dict[str, Dict[str, int]]):
    qrels_ranx = Qrels(qrels)
    run_ranx   = Run(run_dict)

    metrics = [
        "ndcg@1", "ndcg@3", "ndcg@5", "ndcg@10",
        "map", "mrr", "mrr@10", "precision@10", "recall@10", "recall@100",
    ]

    scores = evaluate(qrels_ranx, run_ranx, metrics=metrics)
    for m in metrics:
        print(f"{m:>12}: {scores[m]:.4f}")

In [53]:
import numpy as np

def print_latency_stats(latencies: List[float]):
    l = np.array(latencies)

    print(f"Count    : {len(l)}")
    print(f"Mean     : {l.mean():.4f} sec")
    print(f"Median   : {np.median(l):.4f} sec")
    print(f"p90      : {np.percentile(l,90):.4f} sec")
    print(f"p95      : {np.percentile(l,95):.4f} sec")
    print(f"p99      : {np.percentile(l,99):.4f} sec")
    print(f"Min/Max  : {l.min():.4f} / {l.max():.4f} sec")

In [64]:
evaluate_run_dict(muvera_search_run_dict, qrels)
print_latency_stats(muvera_search_latencies)

      ndcg@1: 0.7169
      ndcg@3: 0.5892
      ndcg@5: 0.5445
     ndcg@10: 0.5144
         map: 0.4426
         mrr: 0.7943
      mrr@10: 0.7910
precision@10: 0.3332
   recall@10: 0.4133
  recall@100: 1.0000
Count    : 1667
Mean     : 0.1789 sec
Median   : 0.1759 sec
p90      : 0.2274 sec
p95      : 0.2413 sec
p99      : 0.3431 sec
Min/Max  : 0.0272 / 0.5739 sec


## BM25 全文検索による評価

WeaviateのBM25検索機能を使用して、全文検索での性能を評価します。

In [26]:
# BM25検索用のコレクションを作成（既存コレクションを再利用可能）
BM25_CLASS_NAME = "jqara_bm25"

from weaviate.classes.config import Configure, Property, DataType

if client.collections.exists(BM25_CLASS_NAME):
    client.collections.delete(BM25_CLASS_NAME)

client.collections.create(
    name=BM25_CLASS_NAME,
    # BM25はデフォルトで有効なので特別な設定は不要
    # 転置インデックスの設定をカスタマイズする場合は inverted_index_config を使用
    properties=[
        Property(name="d_id", data_type=DataType.TEXT),
        Property(name="title", data_type=DataType.TEXT),
        Property(name="text", data_type=DataType.TEXT),
    ],
)

In [27]:
# BM25コレクションにデータをアップロード
bm25_col = client.collections.get(BM25_CLASS_NAME)

total = len(subset)

with bm25_col.batch.fixed_size(batch_size=100) as batch, tqdm(total=total, desc="📤 Uploading to BM25 collection") as pbar:
    for obj in subset:
        batch.add_object(
            properties={
                "d_id": obj["id"],
                "text": obj["text"],
                "title": obj["title"],
            },
        )
        pbar.update(1)

if bm25_col.batch.failed_objects:
    print(f"\n❌ Number of failed imports: {len(bm25_col.batch.failed_objects)}")
else:
    print("\n✅ All objects uploaded successfully!")

count = bm25_col.aggregate.over_all(total_count=True).total_count
print(f"🧮 BM25コレクション登録件数: {count}")

📤 Uploading to BM25 collection: 100%|██████████| 66700/66700 [00:08<00:00, 8318.38it/s]


✅ All objects uploaded successfully!
🧮 BM25コレクション登録件数: 66700


In [29]:
# BM25検索の動作確認
from weaviate.classes.query import MetadataQuery

q = subset[0]["question"]
print(f"Query: {q}\n")

# BM25検索（キーワード検索）
response = bm25_col.query.bm25(
    query=q,
    query_properties=["text", "title"],  # 検索対象プロパティ
    limit=10,
    return_metadata=MetadataQuery(score=True)
)

for o in response.objects:
    title = o.properties.get("title", "")
    text = o.properties.get("text", "")[:80]
    score = o.metadata.score
    print(f"- score={score:.4f}  title: {title}")
    print(f"  text: {text}...\n")

Query: 摂氏ではマイナス273.15度にあたる、全ての原子の振動が停止する最も低い温度を何というでしょう?



In [30]:
# BM25検索用の非同期検索関数
from typing import List, Tuple
import time

async def async_bm25_search(async_col, q: str, topk: int = 100) -> Tuple[List[Tuple[str, float]], float]:
    """
    BM25を用いた非同期全文検索関数
    
    Args:
        async_col: 非同期Weaviateコレクション
        q: 検索クエリ文字列
        topk: 取得する件数
        
    Returns:
        ([(doc_id, score), ...], elapsed) のタプル
    """
    start = time.perf_counter()

    response = await async_col.query.bm25(
        query=q,
        query_properties=["text", "title"],
        limit=topk,
        return_metadata=MetadataQuery(score=True)
    )

    elapsed = time.perf_counter() - start

    results: List[Tuple[str, float]] = []
    for obj in response.objects:
        doc_id = obj.properties.get("d_id", "")
        score = obj.metadata.score
        results.append((doc_id, score))

    return results, elapsed


def create_bm25_search_fn(async_col):
    """async_colをバインドした検索関数を返すファクトリ"""
    async def search_fn(q: str, topk: int = 100) -> Tuple[List[Tuple[str, float]], float]:
        return await async_bm25_search(async_col, q, topk)
    return search_fn

In [31]:
# BM25検索で全クエリを実行

bm25_search_run_dict = {}
bm25_search_latencies = []

async with weaviate.use_async_with_local() as async_client:
    async_col = async_client.collections.get(BM25_CLASS_NAME)
    
    search_fn = create_bm25_search_fn(async_col)
    
    bm25_search_run_dict, bm25_search_latencies = await build_run_dict_async(
        search_fn, 
        qid_to_query,
        topk=10
    )

print(f"検索完了: {len(bm25_search_run_dict)} クエリ")
print(f"平均レイテンシ: {sum(bm25_search_latencies) / len(bm25_search_latencies):.4f} 秒")

Searching: 100%|██████████| 667/667 [00:22<00:00, 29.37it/s]

検索完了: 667 クエリ
平均レイテンシ: 0.3388 秒


In [32]:
# BM25検索の評価結果
print("=" * 50)
print("BM25 全文検索の評価結果")
print("=" * 50)
evaluate_run_dict(bm25_search_run_dict, qrels)
print()
print_latency_stats(bm25_search_latencies)

BM25 全文検索の評価結果
      ndcg@1: 0.1739
      ndcg@3: 0.1384
      ndcg@5: 0.1287
     ndcg@10: 0.1182
         map: 0.0611
         mrr: 0.2175
precision@10: 0.0786
   recall@10: 0.0933
  recall@100: 0.0933

Count    : 667
Mean     : 0.3388 sec
Median   : 0.2785 sec
p90      : 0.5393 sec
p95      : 0.6775 sec
p99      : 0.9312 sec
Min/Max  : 0.0850 / 0.9958 sec


## 結果比較: MUVERA vs BM25

In [33]:
# 結果を並べて比較
import pandas as pd
from ranx import Qrels, Run, evaluate

def get_metrics(run_dict, qrels):
    qrels_ranx = Qrels(qrels)
    run_ranx = Run(run_dict)
    metrics = ["ndcg@1", "ndcg@3", "ndcg@5", "ndcg@10", "map", "mrr", "precision@10", "recall@10"]
    return evaluate(qrels_ranx, run_ranx, metrics=metrics)

muvera_scores = get_metrics(muvera_search_run_dict, qrels)
bm25_scores = get_metrics(bm25_search_run_dict, qrels)

comparison_data = {
    "Metric": ["ndcg@1", "ndcg@3", "ndcg@5", "ndcg@10", "map", "mrr", "precision@10", "recall@10"],
    "MUVERA": [muvera_scores[m] for m in ["ndcg@1", "ndcg@3", "ndcg@5", "ndcg@10", "map", "mrr", "precision@10", "recall@10"]],
    "BM25": [bm25_scores[m] for m in ["ndcg@1", "ndcg@3", "ndcg@5", "ndcg@10", "map", "mrr", "precision@10", "recall@10"]],
}

df = pd.DataFrame(comparison_data)
df["Diff (MUVERA - BM25)"] = df["MUVERA"] - df["BM25"]

print("=" * 70)
print("検索手法比較: MUVERA (ColBERT Multi-Vector) vs BM25 (全文検索)")
print("=" * 70)
print(df.to_string(index=False, float_format="{:.4f}".format))

print("\n--- レイテンシ比較 ---")
print(f"MUVERA 平均: {sum(muvera_search_latencies)/len(muvera_search_latencies):.4f} sec")
print(f"BM25   平均: {sum(bm25_search_latencies)/len(bm25_search_latencies):.4f} sec")

検索手法比較: MUVERA (ColBERT Multi-Vector) vs BM25 (全文検索)
      Metric  MUVERA   BM25  Diff (MUVERA - BM25)
      ndcg@1  0.1769 0.1739                0.0030
      ndcg@3  0.1925 0.1384                0.0541
      ndcg@5  0.2039 0.1287                0.0753
     ndcg@10  0.3109 0.1182                0.1927
         map  0.1276 0.0611                0.0665
         mrr  0.3479 0.2175                0.1304
precision@10  0.3082 0.0786                0.2297
   recall@10  0.3398 0.0933                0.2465

--- レイテンシ比較 ---
MUVERA 平均: 0.1842 sec
BM25   平均: 0.3388 sec


## Ruri-v3 ベクトル検索による評価

日本語特化の埋め込みモデル [ruri-v3-310m](https://huggingface.co/cl-nagoya/ruri-v3-310m) を使用した通常のベクトル検索で評価します。

| モデル | パラメータ | ベクトル次元 |
|--------|-----------|-------------|
| ruri-v3-30m | 36.7M | 256 |
| ruri-v3-70m | 70M | 384 |
| ruri-v3-130m | 130M | 512 |
| **ruri-v3-310m** | 310M | **768** |

精度重視のため最大モデル（768次元）を使用します。

In [35]:
# Ruri-v3モデルのロード
from sentence_transformers import SentenceTransformer

ruri_model = SentenceTransformer("cl-nagoya/ruri-v3-310m")
print(f"モデルロード完了: {ruri_model}")
print(f"ベクトル次元: {ruri_model.get_sentence_embedding_dimension()}")

ValueError: The checkpoint you are trying to load has model type `modernbert` but Transformers does not recognize this architecture. This could be because of an issue with the checkpoint, or because your version of Transformers is out of date.

In [ ]:
# Ruri-v3用コレクション作成
RURI_CLASS_NAME = "jqara_ruri"

from weaviate.classes.config import Configure, Property, DataType, VectorDistances

if client.collections.exists(RURI_CLASS_NAME):
    client.collections.delete(RURI_CLASS_NAME)

client.collections.create(
    name=RURI_CLASS_NAME,
    vector_config=[
        Configure.Vectors.none(
            name="ruri_vector",
            # HNSWインデックス設定
            vector_index_config=Configure.VectorIndex.hnsw(
                distance_metric=VectorDistances.COSINE,  # ruri-v3は正規化済みなのでcosine推奨
            ),
        ),
    ],
    properties=[
        Property(name="d_id", data_type=DataType.TEXT),
        Property(name="title", data_type=DataType.TEXT),
        Property(name="text", data_type=DataType.TEXT),
    ],
)
print(f"✅ コレクション '{RURI_CLASS_NAME}' 作成完了")

In [ ]:
# ドキュメントのエンベディング生成（バッチ処理）
# ruri-v3では検索対象文書に "検索文書: " プレフィックスを付ける

doc_texts = [f"検索文書: {obj['title']} {obj['text']}" for obj in subset]

print(f"📝 {len(doc_texts)} 件のドキュメントをエンベディング中...")
ruri_doc_embeddings = ruri_model.encode(
    doc_texts, 
    batch_size=64, 
    show_progress_bar=True,
    convert_to_numpy=True
)
print(f"✅ エンベディング完了: shape={ruri_doc_embeddings.shape}")

In [ ]:
# Weaviateにアップロード
ruri_col = client.collections.get(RURI_CLASS_NAME)

total = len(subset)

with ruri_col.batch.fixed_size(batch_size=100) as batch, tqdm(total=total, desc="📤 Uploading to Ruri collection") as pbar:
    for obj, emb in zip(subset, ruri_doc_embeddings):
        batch.add_object(
            properties={
                "d_id": obj["id"],
                "text": obj["text"],
                "title": obj["title"],
            },
            vector={"ruri_vector": emb.tolist()},
        )
        pbar.update(1)

if ruri_col.batch.failed_objects:
    print(f"\n❌ Number of failed imports: {len(ruri_col.batch.failed_objects)}")
else:
    print("\n✅ All objects uploaded successfully!")

count = ruri_col.aggregate.over_all(total_count=True).total_count
print(f"🧮 Ruriコレクション登録件数: {count}")

In [ ]:
# Ruri検索の動作確認
q = subset[0]["question"]
print(f"Query: {q}\n")

# クエリには "検索クエリ: " プレフィックスを付ける
q_emb = ruri_model.encode(f"検索クエリ: {q}", convert_to_numpy=True)

response = ruri_col.query.near_vector(
    near_vector=q_emb.tolist(),
    target_vector="ruri_vector",
    limit=10,
    return_metadata=MetadataQuery(distance=True)
)

for o in response.objects:
    title = o.properties.get("title", "")
    text = o.properties.get("text", "")[:80]
    dist = o.metadata.distance
    print(f"- distance={dist:.4f}  title: {title}")
    print(f"  text: {text}...\n")

In [ ]:
# Ruri検索用の非同期検索関数
async def async_ruri_search(async_col, ruri_model, q: str, topk: int = 100) -> Tuple[List[Tuple[str, float]], float]:
    """
    Ruri-v3を用いた非同期ベクトル検索関数
    
    Args:
        async_col: 非同期Weaviateコレクション
        ruri_model: SentenceTransformerモデル
        q: 検索クエリ文字列
        topk: 取得する件数
        
    Returns:
        ([(doc_id, score), ...], elapsed) のタプル
    """
    # クエリのエンベディング（"検索クエリ: " プレフィックス付き）
    q_emb = ruri_model.encode(f"検索クエリ: {q}", convert_to_numpy=True)

    start = time.perf_counter()

    response = await async_col.query.near_vector(
        near_vector=q_emb.tolist(),
        target_vector="ruri_vector",
        limit=topk,
        return_metadata=MetadataQuery(distance=True)
    )

    elapsed = time.perf_counter() - start

    results: List[Tuple[str, float]] = []
    for obj in response.objects:
        doc_id = obj.properties.get("d_id", "")
        # distanceを負にしてスコアとして扱う（小さいほど良い → 大きいほど良いに変換）
        score = -obj.metadata.distance
        results.append((doc_id, score))

    return results, elapsed


def create_ruri_search_fn(async_col, ruri_model):
    """async_colとruri_modelをバインドした検索関数を返すファクトリ"""
    async def search_fn(q: str, topk: int = 100) -> Tuple[List[Tuple[str, float]], float]:
        return await async_ruri_search(async_col, ruri_model, q, topk)
    return search_fn

In [ ]:
# Ruri検索で全クエリを実行

ruri_search_run_dict = {}
ruri_search_latencies = []

async with weaviate.use_async_with_local() as async_client:
    async_col = async_client.collections.get(RURI_CLASS_NAME)
    
    search_fn = create_ruri_search_fn(async_col, ruri_model)
    
    ruri_search_run_dict, ruri_search_latencies = await build_run_dict_async(
        search_fn, 
        qid_to_query,
        topk=10
    )

print(f"検索完了: {len(ruri_search_run_dict)} クエリ")
print(f"平均レイテンシ: {sum(ruri_search_latencies) / len(ruri_search_latencies):.4f} 秒")

In [ ]:
# Ruri検索の評価結果
print("=" * 50)
print("Ruri-v3 ベクトル検索の評価結果")
print("=" * 50)
evaluate_run_dict(ruri_search_run_dict, qrels)
print()
print_latency_stats(ruri_search_latencies)

## 全手法の比較: MUVERA vs BM25 vs Ruri-v3

In [ ]:
# 3手法の比較
ruri_scores = get_metrics(ruri_search_run_dict, qrels)

comparison_data_all = {
    "Metric": ["ndcg@1", "ndcg@3", "ndcg@5", "ndcg@10", "map", "mrr", "precision@10", "recall@10"],
    "MUVERA (ColBERT)": [muvera_scores[m] for m in ["ndcg@1", "ndcg@3", "ndcg@5", "ndcg@10", "map", "mrr", "precision@10", "recall@10"]],
    "Ruri-v3 (Dense)": [ruri_scores[m] for m in ["ndcg@1", "ndcg@3", "ndcg@5", "ndcg@10", "map", "mrr", "precision@10", "recall@10"]],
    "BM25 (Sparse)": [bm25_scores[m] for m in ["ndcg@1", "ndcg@3", "ndcg@5", "ndcg@10", "map", "mrr", "precision@10", "recall@10"]],
}

df_all = pd.DataFrame(comparison_data_all)

print("=" * 80)
print("検索手法比較: MUVERA (ColBERT) vs Ruri-v3 (Dense Vector) vs BM25 (Sparse)")
print("=" * 80)
print(df_all.to_string(index=False, float_format="{:.4f}".format))

print("\n" + "=" * 80)
print("レイテンシ比較 (Weaviate検索のみ、エンベディング生成時間は除く)")
print("=" * 80)
print(f"MUVERA   平均: {sum(muvera_search_latencies)/len(muvera_search_latencies):.4f} sec")
print(f"Ruri-v3  平均: {sum(ruri_search_latencies)/len(ruri_search_latencies):.4f} sec")
print(f"BM25     平均: {sum(bm25_search_latencies)/len(bm25_search_latencies):.4f} sec")